# Error analysis
- similar to [error_analysis_v1.ipynb](https://nbviewer.org/urls/cluster.klima.uni-bremen.de/~lschuster/error_analysis/error_analysis_v1.ipynb?flush_cache=true#Analysis-for-Level-5-pre-processing-directories!)

In [1]:
from oggm import cfg, workflow, utils, shop
import pandas as pd
import os, glob
import numpy as np
import xarray as xr
import seaborn as sns
import matplotlib.pyplot as plt
sns.set_style("whitegrid")

cfg.initialize()

import matplotlib
matplotlib.rcParams['figure.figsize'] = (14, 8)
import geopandas as gpd

gcms_cmip6 = pd.read_csv('/home/www/oggm/cmip6/all_gcm_list.csv', index_col=0)   

gcms = []
ssps = []
gcms_ssps = []
for ind in gcms_cmip6.loc[gcms_cmip6['var']=='pr'].index:
    gcms.append(gcms_cmip6.loc[ind].gcm)
    ssps.append(gcms_cmip6.loc[ind].ssp)
    gcms_ssps.append(f'{gcms_cmip6.loc[ind].gcm}_{gcms_cmip6.loc[ind].ssp}')

2023-06-05 07:42:38: oggm.cfg: Reading default parameters from the OGGM `params.cfg` configuration file.
2023-06-05 07:42:38: oggm.cfg: Multiprocessing switched OFF according to the parameter file.
2023-06-05 07:42:38: oggm.cfg: Multiprocessing: using all available processors (N=32)


## Get a list with the amount of failing glaciers and area for the different Scenarios and GCMs

In [4]:
pd_geodetic = utils.get_geodetic_mb_dataframe()[utils.get_geodetic_mb_dataframe().period=='2000-01-01_2020-01-01']
# ok, connectivity level 2 glaciers are not inside ...
rgis_05 = gpd.read_file(utils.get_rgi_region_file('05', version='62'))
rgis_05_remove = rgis_05.loc[(rgis_05['Connect'] ==2)].RGIId.values
assert len(np.intersect1d(pd_geodetic.index.values,rgis_05_remove)) == 0
total_area = pd_geodetic.area.sum()
total_counts = len(pd_geodetic)

In [ ]:
# NEW version 2023.3:
for hist in ['w5e5_gcm_merged', 'gcm_from_2000']:
    for bc in ['_bc_2000_2019']: #,'_bc_1979_2014'
        pd_working = pd.DataFrame(index = pd_geodetic.index,
                      columns=gcms_ssps)
        # we will set those that are not running afterwards to np.NaN value
        pd_working.loc[pd_geodetic.index] = True
        pd_working['area'] = pd_geodetic.area
        pd_working['all_running_rgis'] = np.NaN
        pd_working['rgi_reg'] = pd_geodetic.reg
        for rgi_reg in np.array([ 1,  2,  3,  4, 6,  7,  8,  9,
                                 10, 11, 12, 13, 14, 15, 16, 17, 18, 19, 5]):
            print(rgi_reg)
            if rgi_reg < 10:
                rgi_reg_s = f'0{rgi_reg}'
            else:
                rgi_reg_s = rgi_reg
                

            dpath = f'/home/www/lschuster/runs_oggm_v16/runs_2023.3/output/RGI{rgi_reg_s}'
            # amount of glaciers in that rgi region
            rgi_reg_glaciers = pd_working.loc[pd_working.rgi_reg==int(rgi_reg)].index
            for gcm_ssp in gcms_ssps:    
                with xr.open_mfdataset(f'{dpath}/run_hydro_{hist}_endyr2100_CMIP6_{gcm_ssp}{bc}_rgi{rgi_reg_s}*.nc') as ds:
                    ds = ds.volume.sel(time=2000).load()
                # make sure that all glaciers have been running
                assert len(ds.rgi_id.values) == len(rgi_reg_glaciers)
                rgis_error = list(set(rgi_reg_glaciers) - set(ds.dropna(dim='rgi_id').rgi_id.values))
                pd_working.loc[rgis_error, gcm_ssp] = np.NaN
                ds.close()
            
        all_running_rgis = pd_working[gcms_ssps].dropna().index
        pd_working.loc[all_running_rgis, 'all_running_rgis'] = True
        all_running_rel = len(all_running_rgis)*100/len(pd_geodetic)
        all_running_rel_area = pd_working.loc[all_running_rgis].area.sum()*100/pd_working.area.sum()
        print(f'{bc}_{hist}')
        print(f'Amount of glaciers that run over the entire time period: {len(all_running_rgis)}')
        print(f'Relative percentage of glacier amount where all gcms and ssp could run over the entire time period: {all_running_rel:0.2f}%')
        print(f'Relative percentage of glacier area where all gcms and ssp could run over the entire time period: {all_running_rel_area:0.2f}%')
        #pd_rel_error_area_L5.to_csv('rel_error_area_statistics_for_oversh_stab_scenarios.csv')
        pd_working.to_csv(f'working_rgis_for_oggm_v16_CMIP6{bc}_{hist}_2023.3.csv')


1
2
3
4
6
7
8
9
10
11
12
13
14
15
16
17
18
19
5
_bc_2000_2019_w5e5_gcm_merged
Amount of glaciers that run over the entire time period: 213655
Relative percentage of glacier amount where all gcms and ssp could run over the entire time period: 99.12%
Relative percentage of glacier area where all gcms and ssp could run over the entire time period: 99.90%
1


In [ ]:
run = False
if run:
    for hist in ['w5e5_gcm_merged', 'gcm_from_2000']:
        for bc in ['_bc_2000_2019']: #,'_bc_1979_2014'
            pd_working = pd.DataFrame(index = pd_geodetic.index,
                          columns=gcms_ssps)
            # we will set those that are not running afterwards to np.NaN value
            pd_working.loc[pd_geodetic.index] = True
            pd_working['area'] = pd_geodetic.area
            pd_working['all_running_rgis'] = np.NaN
            pd_working['rgi_reg'] = pd_geodetic.reg
            for rgi_reg in np.array([ 1,  2,  3,  4, 6,  7,  8,  9,
                                     10, 11, 12, 13, 14, 15, 16, 17, 18, 19, 5]):
                print(rgi_reg)
                if rgi_reg < 10:
                    rgi_reg_s = f'0{rgi_reg}'
                else:
                    rgi_reg_s = rgi_reg


                dpath = f'/home/www/lschuster/runs_oggm_v16/output/RGI{rgi_reg_s}'
                # amount of glaciers in that rgi region
                rgi_reg_glaciers = pd_working.loc[pd_working.rgi_reg==int(rgi_reg)].index
                for gcm_ssp in gcms_ssps:    
                    with xr.open_mfdataset(f'{dpath}/run_hydro_{hist}_endyr2100_CMIP6_{gcm_ssp}{bc}_rgi{rgi_reg_s}*.nc') as ds:
                        ds = ds.volume.sel(time=2000).load()
                    # make sure that all glaciers have been running
                    assert len(ds.rgi_id.values) == len(rgi_reg_glaciers)
                    rgis_error = list(set(rgi_reg_glaciers) - set(ds.dropna(dim='rgi_id').rgi_id.values))
                    pd_working.loc[rgis_error, gcm_ssp] = np.NaN
                    ds.close()

            all_running_rgis = pd_working[gcms_ssps].dropna().index
            pd_working.loc[all_running_rgis, 'all_running_rgis'] = True
            all_running_rel = len(all_running_rgis)*100/len(pd_geodetic)
            all_running_rel_area = pd_working.loc[all_running_rgis].area.sum()*100/pd_working.area.sum()
            print(f'{bc}_{hist}')
            print(f'Amount of glaciers that run over the entire time period: {len(all_running_rgis)}')
            print(f'Relative percentage of glacier amount where all gcms and ssp could run over the entire time period: {all_running_rel:0.2f}%')
            print(f'Relative percentage of glacier area where all gcms and ssp could run over the entire time period: {all_running_rel_area:0.2f}%')
            #pd_rel_error_area_L5.to_csv('rel_error_area_statistics_for_oversh_stab_scenarios.csv')
            pd_working.to_csv(f'working_rgis_for_oggm_v16_CMIP6{bc}_{hist}.csv')


##### Do the same for every RGI region:

In [ ]:
# NEW version 2023.3:
for rgi_reg in pd_working.rgi_reg.unique():
    if rgi_reg < 10:
        rgi_reg_s = f'0{rgi_reg}'
    else:
        rgi_reg_s = rgi_reg
    print(f'RGI{rgi_reg_s}')
    for hist in ['w5e5_gcm_merged', 'gcm_from_2000']:
        pd_working = pd.read_csv(f'working_rgis_for_oggm_v16_CMIP6{bc}_{hist}_2023.3.csv', low_memory=False)
        pd_working_sel = pd_working.loc[pd_working.rgi_reg==int(rgi_reg)]
        all_running_rgis_reg = pd_working_sel[gcms_ssps].dropna().index
        all_running_rel_reg = len(all_running_rgis_reg)*100/len(pd_working_sel)
        all_running_rel_area_reg = pd_working.loc[all_running_rgis_reg].area.sum()*100/pd_working_sel.area.sum()
        print(f'{hist}')
        print(f'Amount of glaciers that run over the entire time period: {len(all_running_rgis_reg)}')
        print(f'Relative percentage of glacier amount where all gcms and ssp could run over the entire time period: {all_running_rel_reg:0.2f}%')
        print(f'Relative percentage of glacier area where all gcms and ssp could run over the entire time period: {all_running_rel_area_reg:0.2f}%')

In [11]:
for rgi_reg in pd_working.rgi_reg.unique():
    if rgi_reg < 10:
        rgi_reg_s = f'0{rgi_reg}'
    else:
        rgi_reg_s = rgi_reg
    print(f'RGI{rgi_reg_s}')
    for hist in ['w5e5_gcm_merged', 'gcm_from_2000']:
        pd_working = pd.read_csv(f'working_rgis_for_oggm_v16_CMIP6{bc}_{hist}.csv', low_memory=False)
        pd_working_sel = pd_working.loc[pd_working.rgi_reg==int(rgi_reg)]
        all_running_rgis_reg = pd_working_sel[gcms_ssps].dropna().index
        all_running_rel_reg = len(all_running_rgis_reg)*100/len(pd_working_sel)
        all_running_rel_area_reg = pd_working.loc[all_running_rgis_reg].area.sum()*100/pd_working_sel.area.sum()
        print(f'{hist}')
        print(f'Amount of glaciers that run over the entire time period: {len(all_running_rgis_reg)}')
        print(f'Relative percentage of glacier amount where all gcms and ssp could run over the entire time period: {all_running_rel_reg:0.2f}%')
        print(f'Relative percentage of glacier area where all gcms and ssp could run over the entire time period: {all_running_rel_area_reg:0.2f}%')

RGI01
w5e5_gcm_merged
Amount of glaciers that run over the entire time period: 27086
Relative percentage of glacier amount where all gcms and ssp could run over the entire time period: 99.92%
Relative percentage of glacier area where all gcms and ssp could run over the entire time period: 99.99%
gcm_from_2000
Amount of glaciers that run over the entire time period: 27085
Relative percentage of glacier amount where all gcms and ssp could run over the entire time period: 99.92%
Relative percentage of glacier area where all gcms and ssp could run over the entire time period: 99.99%
RGI02
w5e5_gcm_merged
Amount of glaciers that run over the entire time period: 18805
Relative percentage of glacier amount where all gcms and ssp could run over the entire time period: 99.73%
Relative percentage of glacier area where all gcms and ssp could run over the entire time period: 99.98%
gcm_from_2000
Amount of glaciers that run over the entire time period: 18797
Relative percentage of glacier amount wh

***Save it in a common running file with just _bc_2000_2019****

In [ ]:
all_running_rgis_l = []
for hist in ['w5e5_gcm_merged', 'gcm_from_2000']:
    for bc in ['_bc_2000_2019']:
        pd_working = pd.read_csv(f'working_rgis_for_oggm_v16_CMIP6{bc}_{hist}_2023.3.csv', low_memory=False, index_col='rgiid')
        all_running_rgis_l.append(pd_working['all_running_rgis'].dropna().index)
        
for hist in ['w5e5_gcm_merged', 'gcm_from_2000']:
    for bc in ['_bc_2000_2019']:
        pd_working = pd.read_csv(f'working_rgis_for_oggm_v16_CMIP6{bc}_{hist}.csv', low_memory=False, index_col='rgiid')
        all_running_rgis_l.append(pd_working['all_running_rgis'].dropna().index)

all_running_rgis = all_running_rgis_l[0]
for i in all_running_rgis_l[1:]:
    all_running_rgis = list(set(all_running_rgis).intersection(i))
pd_working_all = pd_working.loc[all_running_rgis][['area','all_running_rgis', 'rgi_reg']]
pd_working_all.to_csv('all_common_working_rgi_ids_bc_2000_2019_w_2023.2_vs_2023.3.csv')

### Now repeat it with the CMIP6 run with '_bc_1979_2014'

In [12]:
for hist in ['w5e5_gcm_merged', 'gcm_from_2000']:
    for bc in ['_bc_1979_2014']:
        pd_working = pd.DataFrame(index = pd_geodetic.index,
                      columns=gcms_ssps)
        # we will set those that are not running afterwards to np.NaN value
        pd_working.loc[pd_geodetic.index] = True
        pd_working['area'] = pd_geodetic.area
        pd_working['all_running_rgis'] = np.NaN
        pd_working['rgi_reg'] = pd_geodetic.reg
        for rgi_reg in np.array([ 1,  2,  3,  4, 6,  7,  8,  9,
                                 10, 11, 12, 13, 14, 15, 16, 17, 18, 19, 5]):
            print(rgi_reg)
            if rgi_reg < 10:
                rgi_reg_s = f'0{rgi_reg}'
            else:
                rgi_reg_s = rgi_reg
                

            dpath = f'/home/www/lschuster/runs_oggm_v16/output/RGI{rgi_reg_s}'
            # amount of glaciers in that rgi region
            rgi_reg_glaciers = pd_working.loc[pd_working.rgi_reg==int(rgi_reg)].index
            for gcm_ssp in gcms_ssps:
                gcm = gcm_ssp.split('_')[0]
                ssp = gcm_ssp.split('_')[1]
                if gcm.lower() in ['gfdl-esm4', 'mpi-esm1-2-hr', 'mri-esm2-0']: 
                    if ssp in ['ssp126', 'ssp370', 'ssp585']:
                        with xr.open_mfdataset(f'{dpath}/run_hydro_{hist}_endyr2100_CMIP6_{gcm_ssp}{bc}_rgi{rgi_reg_s}*.nc') as ds:
                            ds = ds.volume.sel(time=2000).load()
                            # make sure that all glaciers have been running
                            assert len(ds.rgi_id.values) == len(rgi_reg_glaciers)
                            rgis_error = list(set(rgi_reg_glaciers) - set(ds.dropna(dim='rgi_id').rgi_id.values))
                            pd_working.loc[rgis_error, gcm_ssp] = np.NaN
                        ds.close()
            
        all_running_rgis = pd_working[gcms_ssps].dropna().index
        pd_working.loc[all_running_rgis, 'all_running_rgis'] = True
        all_running_rel = len(all_running_rgis)*100/len(pd_geodetic)
        all_running_rel_area = pd_working.loc[all_running_rgis].area.sum()*100/pd_working.area.sum()
        print(f'{bc}_{hist}')
        print(f'Amount of glaciers that run over the entire time period: {len(all_running_rgis)}')
        print(f'Relative percentage of glacier amount where all gcms and ssp could run over the entire time period: {all_running_rel:0.2f}%')
        print(f'Relative percentage of glacier area where all gcms and ssp could run over the entire time period: {all_running_rel_area:0.2f}%')
        #pd_rel_error_area_L5.to_csv('rel_error_area_statistics_for_oversh_stab_scenarios.csv')
        pd_working.to_csv(f'working_rgis_for_oggm_v16_CMIP6{bc}_{hist}.csv')


1
2
3
4
6
7
8
9
10
11
12
13
14
15
16
17
18
19
5
_bc_1979_2014_w5e5_gcm_merged
Amount of glaciers that run over the entire time period: 214055
Relative percentage of glacier amount where all gcms and ssp could run over the entire time period: 99.31%
Relative percentage of glacier area where all gcms and ssp could run over the entire time period: 99.91%
1
2
3
4
6
7
8
9
10
11
12
13
14
15
16
17
18
19
5
_bc_1979_2014_gcm_from_2000
Amount of glaciers that run over the entire time period: 213997
Relative percentage of glacier amount where all gcms and ssp could run over the entire time period: 99.28%
Relative percentage of glacier area where all gcms and ssp could run over the entire time period: 99.90%


### Now repeat it with the ISIMIP3b runs

In [13]:
isimip3b_members = ['gfdl-esm4_r1i1p1f1', 'mpi-esm1-2-hr_r1i1p1f1',
                        'mri-esm2-0_r1i1p1f1',
                        'ipsl-cm6a-lr_r1i1p1f1', 'ukesm1-0-ll_r1i1p1f2' ]
gcms_ssps_isimip3b = []
for member in isimip3b_members:
    # Download the three main SSPs
    for ssp in ['ssp126', 'ssp370','ssp585']:
        gcms_ssps_isimip3b.append(f'{member}_{ssp}')

In [17]:
pd_working#.dropna()

CESM2-WACCM_ssp126 CESM2-WACCM_ssp370 CESM2-WACCM_ssp585  \
rgiid                                                                     
RGI60-01.00001               True               True               True   
RGI60-01.00002               True               True               True   
RGI60-01.00003               True               True               True   
RGI60-01.00004               True               True               True   
RGI60-01.00005               True               True               True   
...                           ...                ...                ...   
RGI60-19.02748               True               True               True   
RGI60-19.02749               True               True               True   
RGI60-19.02750               True               True               True   
RGI60-19.02751               True               True               True   
RGI60-19.02752               True               True               True   

               CESM2-WACCM_ssp245 CESM2-WACCM_ssp534-over  \
rgiid                                                       
RGI60-01.00001               True                    True   
RGI60-01.00002               True                    True   
RGI60-01.00003               True                    True   
RGI60-01.00004               True                    True   
RGI60-01.00005               True                    True   
...                           ...                     ...   
RGI60-19.02748               True                    True   
RGI60-19.02749               True                    True   
RGI60-19.02750               True                    True   
RGI60-19.02751               True                    True   
RGI60-19.02752               True                    True   

               MPI-ESM1-2-HR_ssp585 MPI-ESM1-2-HR_ssp370 MPI-ESM1-2-HR_ssp245  \
rgiid                                                                           
RGI60-01.00001                 True                 True                 True   
RGI60-01.00002                 True                 True                 True   
RGI60-01.00003                 True                 True                 True   
RGI60-01.00004                 True                 True                 True   
RGI60-01.00005                 True                 True                 True   
...                             ...                  ...                  ...   
RGI60-19.02748                 True                 True                 True   
RGI60-19.02749                 True                 True                 True   
RGI60-19.02750                 True                 True                 True   
RGI60-19.02751                 True                 True                 True   
RGI60-19.02752                 True                 True                 True   

               MPI-ESM1-2-HR_ssp126 GFDL-ESM4_ssp370  ...  \
rgiid                                                 ...   
RGI60-01.00001                 True             True  ...   
RGI60-01.00002                 True             True  ...   
RGI60-01.00003                 True             True  ...   
RGI60-01.00004                 True             True  ...   
RGI60-01.00005                 True             True  ...   
...                             ...              ...  ...   
RGI60-19.02748                 True             True  ...   
RGI60-19.02749                 True             True  ...   
RGI60-19.02750                 True             True  ...   
RGI60-19.02751                 True             True  ...   
RGI60-19.02752                 True             True  ...   

               gfdl-esm4_r1i1p1f1_ssp585 mpi-esm1-2-hr_r1i1p1f1_ssp126  \
rgiid                                                                    
RGI60-01.00001                       NaN                           NaN   
RGI60-01.00002                       NaN                           NaN   
RGI60-01.00003                       NaN                           NaN   
RGI60-01.00004             

In [18]:
gcms_ssps_isimip3b

['gfdl-esm4_r1i1p1f1_ssp126',
 'gfdl-esm4_r1i1p1f1_ssp370',
 'gfdl-esm4_r1i1p1f1_ssp585',
 'mpi-esm1-2-hr_r1i1p1f1_ssp126',
 'mpi-esm1-2-hr_r1i1p1f1_ssp370',
 'mpi-esm1-2-hr_r1i1p1f1_ssp585',
 'mri-esm2-0_r1i1p1f1_ssp126',
 'mri-esm2-0_r1i1p1f1_ssp370',
 'mri-esm2-0_r1i1p1f1_ssp585',
 'ipsl-cm6a-lr_r1i1p1f1_ssp126',
 'ipsl-cm6a-lr_r1i1p1f1_ssp370',
 'ipsl-cm6a-lr_r1i1p1f1_ssp585',
 'ukesm1-0-ll_r1i1p1f2_ssp126',
 'ukesm1-0-ll_r1i1p1f2_ssp370',
 'ukesm1-0-ll_r1i1p1f2_ssp585']

In [19]:
for hist in ['w5e5_gcm_merged', 'gcm_from_2000']:
    for bc in ['','_bc_2000_2019']:
        pd_working = pd.DataFrame(index = pd_geodetic.index,
                      columns=gcms_ssps)
        # we will set those that are not running afterwards to np.NaN value
        pd_working.loc[pd_geodetic.index] = True
        pd_working['area'] = pd_geodetic.area
        pd_working['all_running_rgis'] = np.NaN
        pd_working['rgi_reg'] = pd_geodetic.reg
        for rgi_reg in np.array([ 1,  2,  3,  4, 6,  7,  8,  9,
                                 10, 11, 12, 13, 14, 15, 16, 17, 18, 19, 5]):
            print(rgi_reg)
            if rgi_reg < 10:
                rgi_reg_s = f'0{rgi_reg}'
            else:
                rgi_reg_s = rgi_reg
                

            dpath = f'/home/www/lschuster/runs_oggm_v16/output/RGI{rgi_reg_s}'
            # amount of glaciers in that rgi region
            rgi_reg_glaciers = pd_working.loc[pd_working.rgi_reg==int(rgi_reg)].index
            for gcm_ssp in gcms_ssps_isimip3b:
                gcm = gcm_ssp.split('_')[0]
                ssp = gcm_ssp.split('_')[-1]

                with xr.open_mfdataset(f'{dpath}/run_hydro_{hist}_endyr2100_ISIMIP3b_{gcm_ssp}{bc}_rgi{rgi_reg_s}*.nc') as ds:
                    ds = ds.volume.load()
                # make sure that all glaciers have been running
                assert len(ds.rgi_id.values) == len(rgi_reg_glaciers)
                rgis_error = list(set(rgi_reg_glaciers) - set(ds.dropna(dim='rgi_id').rgi_id.values))
                print(len(rgis_error))
                pd_working.loc[rgis_error, gcm_ssp] = np.NaN
                ds.close()
            
        all_running_rgis = pd_working[gcms_ssps].dropna().index
        pd_working.loc[all_running_rgis, 'all_running_rgis'] = True
        all_running_rel = len(all_running_rgis)*100/len(pd_geodetic)
        all_running_rel_area = pd_working.loc[all_running_rgis].area.sum()*100/pd_working.area.sum()
        print(f'{bc}_{hist}')
        print(f'Amount of glaciers that run over the entire time period: {len(all_running_rgis)}')
        print(f'Relative percentage of glacier amount where all gcms and ssp could run over the entire time period: {all_running_rel:0.2f}%')
        print(f'Relative percentage of glacier area where all gcms and ssp could run over the entire time period: {all_running_rel_area:0.2f}%')
        #pd_rel_error_area_L5.to_csv('rel_error_area_statistics_for_oversh_stab_scenarios.csv')
        pd_working.to_csv(f'working_rgis_for_oggm_v16_ISIMIP3b{bc}_{hist}.csv')


1
23
22
21
26
24
22
22
22
22
23
22
21
21
21
21
2
33
32
32
32
32
32
32
32
32
32
32
32
32
32
32
3
27
33
36
30
37
38
36
44
52
32
34
27
21
21
21
4
23
18
18
22
18
18
14
13
17
13
15
12
12
12
13
6
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
7
0
0
0
0
0
0
0
0
0
0
0
0
0
0
0
8
7
7
7
7
7
7
7
7
7
7
7
7
7
7
7
9
2
2
2
2
2
2
2
2
2
2
2
2
2
2
2
10
141
138
144
140
144
138
138
138
137
139
138
137
138
138
138
11
5
5
5
5
5
5
5
5
5
5
5
5
5
5
5
12
342
342
342
342
342
342
342
342
342
342
342
342
342
342
342
13
218
217
213
221
216
211
216
211
210
217
212
214
209
209
209
14
45
47
30
53
46
31
31
31
30
36
35
33
26
27
28
15
17
16
16
19
18
17
16
16
15
16
16
16
16
14
15
16
3
3
3
3
3
3
3
3
3
3
3
3
3
3
3
17
49
45
44
50
46
47
47
44
43
46
44
44
44
42
42
18
1
1
1
1
1
1
1
1
1
1
1
1
1
1
1
19
473
467
466
469
466
465
466
464
464
472
466
467
472
467
465
5
30
24
25
36
31
35
30
24
25
31
32
31
21
20
21
_w5e5_gcm_merged
Amount of glaciers that run over the entire time period: 215547
Relative percentage of glacier amount where all gcms and ssp 

### Common running glaciers working for all global experiments

In [24]:
all_running_rgis_l = []
for hist in ['w5e5_gcm_merged', 'gcm_from_2000']:
    for bc in ['_bc_2000_2019','_bc_1979_2014']:
        pd_working = pd.read_csv(f'working_rgis_for_oggm_v16_CMIP6{bc}_{hist}.csv', low_memory=False, index_col='rgiid')
        all_running_rgis_l.append(pd_working['all_running_rgis'].dropna().index)
        
for hist in ['w5e5_gcm_merged', 'gcm_from_2000']:
    for bc in ['','_bc_2000_2019']:
        pd_working = pd.read_csv(f'working_rgis_for_oggm_v16_ISIMIP3b{bc}_{hist}.csv', low_memory=False, index_col='rgiid')
        all_running_rgis_l.append(pd_working['all_running_rgis'].dropna().index)

all_running_rgis = all_running_rgis_l[0]
for i in all_running_rgis_l[1:]:
    all_running_rgis = list(set(all_running_rgis).intersection(i))
pd_working_all = pd_working.loc[all_running_rgis][['area','all_running_rgis', 'rgi_reg']]
pd_working_all.to_csv('all_common_working_rgi_ids.csv')

In [ ]:
print(len(pd_working_all)/len(pd_working))

In [ ]:
print(pd_working_all.area.sum()/pd_working.area.sum())